# Clickstream Project

Your client `Kirana Store` is an E-commerce company. The company wants to focus on targeting the right customers  with the right products to increase overall revenue and conversion rate.

`Kirana Store` has provided you with the clickstream data on their website and wants you to tell them the answer to their queries. This will help them improve their understanding about their customers so that they can create better product personalization, marketing campaigns, advertisements, etc.

The data contains the following fields :-

- `webClientID` - Unique ID of browser for every system. (If a visitor is using multiple browsers on a system like Chrome, Safari, then there would be a different web clientid for each browser). 

- `VisitDateTime` - Date and time of visit.

- `ProductID` - Unique ID of product browsed/ clicked by the visitor.

- `Activity` - Type of activity can be browsing (`pageload`) or clicking (`click`) a product

- `device` - Information about the device used by visitor to visit the website
> - `Browser` - Browser used by visitor
> - `OS` - OS used by the visitor

- `user` - Information about registered user or users who have already signed up
> - `UserID` - Unique ID of the user
> - `City` - City of the user
> - `Country` - Country of the user

----
## Connecting to MongoDB

----

In [1]:
# Importing the required libraries
import pymongo
import pandas as pd
from datetime import datetime
import pprint as pp

# Does not allow pprint to sort the fields
pp.sorted = lambda x, key=None: x

In [2]:
# Connect to local MongoDB server
client = pymongo.MongoClient("mongodb://localhost:27017/")

In [3]:
# # Restore database
# !mongorestore /home/avadmin/Desktop/Mongo/Content/Project/Project_data/project
!mongorestore --dir="C:/Program Files/MongoDB/Server/4.2/bin/dump"

2023-07-05T20:14:12.051+0530	preparing collections to restore from
2023-07-05T20:14:12.055+0530	don't know what to do with file "C:\Program Files\MongoDB\Server\4.2\bin\dump\clicks.bson", skipping...
2023-07-05T20:14:12.055+0530	don't know what to do with file "C:\Program Files\MongoDB\Server\4.2\bin\dump\clicks.metadata.json", skipping...
2023-07-05T20:14:12.056+0530	0 document(s) restored successfully. 0 document(s) failed to restore.


In [4]:
# Choose the database
db = client['project']

In [5]:
# Sample document
pp.pprint(
    db.clicks.find_one()
)

{'_id': ObjectId('60df1029ad74d9467c91a932'),
 'webClientID': 'WI100000244987',
 'VisitDateTime': datetime.datetime(2018, 5, 25, 4, 51, 14, 179000),
 'ProductID': 'Pr100037',
 'Activity': 'click',
 'device': {'Browser': 'Firefox', 'OS': 'Windows'},
 'user': {'City': 'Colombo', 'Country': 'Sri Lanka'}}


---
## Overiew of the data

----

Number of documents in the collection

In [6]:
db.clicks.count_documents({})

6100000

---
Minimum date for which the records are present

In [7]:
cur = db.clicks.find({}, {'VisitDateTime': 1, '_id': 0})\
               .sort([('VisitDateTime', pymongo.ASCENDING)])\
               .limit(1)

for doc in cur:
    pp.pprint(doc)

{'VisitDateTime': datetime.datetime(2018, 5, 7, 0, 0, 1, 190000)}


----
Maximum date  for which the records are present

In [8]:
cur = db.clicks.find({}, {'VisitDateTime': 1, '_id': 0})\
               .sort([('VisitDateTime', pymongo.DESCENDING)])\
               .limit(1)

for doc in cur:
    pp.pprint(doc)

{'VisitDateTime': datetime.datetime(2018, 5, 27, 23, 59, 59, 576000)}


----
Number of documents that have `user.UserID` field or number of users who have signed up on the website.

In [9]:
count = db.clicks.count_documents({'user.UserID': {'$exists': True}})
print(count)

602293


---
Unique signed up users in the complete data

In [10]:
len(db.clicks.find({'user.UserID': {'$exists': True}}).distinct('user.UserID'))

34050

---
Unique countries and cities

In [11]:
cur = db.clicks.aggregate([
            {
                '$match': {
                            'user.Country': {'$exists':True},
                            'user.City': {'$exists': True}
                        }
            },
            {
                '$group': {
                                '_id': {
                                            'Country': '$user.Country', 
                                            'City': '$user.City'
                                        }
                        }
            },
            {
                '$sort': {'_id.Country': 1}
            }
        ])

for doc in cur:
    pp.pprint(doc)

{'_id': {'Country': 'Afghanistan', 'City': 'Kabul'}}
{'_id': {'Country': 'Albania', 'City': 'Lezhë'}}
{'_id': {'Country': 'Albania', 'City': 'Kosove'}}
{'_id': {'Country': 'Albania', 'City': 'Shkoder'}}
{'_id': {'Country': 'Albania', 'City': 'Elbasan'}}
{'_id': {'Country': 'Albania', 'City': 'Korçë'}}
{'_id': {'Country': 'Albania', 'City': 'Durrës'}}
{'_id': {'Country': 'Albania', 'City': 'Fier'}}
{'_id': {'Country': 'Albania', 'City': 'Yzberish'}}
{'_id': {'Country': 'Albania', 'City': 'Tirana'}}
{'_id': {'Country': 'Algeria', 'City': 'Tizi Ouzou'}}
{'_id': {'Country': 'Algeria', 'City': 'Ras el Oued'}}
{'_id': {'Country': 'Algeria', 'City': 'Ain Beida'}}
{'_id': {'Country': 'Algeria', 'City': 'Mocta Douz'}}
{'_id': {'Country': 'Algeria', 'City': 'Douéra'}}
{'_id': {'Country': 'Algeria', 'City': 'Laghouat'}}
{'_id': {'Country': 'Algeria', 'City': 'Ouargla'}}
{'_id': {'Country': 'Algeria', 'City': 'El Harrach'}}
{'_id': {'Country': 'Algeria', 'City': 'Commune de Draa Ben Khedda'}}
{'_i

---
Unique `OS`

In [12]:
db.clicks.find().distinct('device.OS')

['Android',
 'BlackBerry OS',
 'Chrome OS',
 'Chromecast',
 'Fedora',
 'FreeBSD',
 'Kindle',
 'Linux',
 'Mac OS X',
 'NetBSD',
 'OpenBSD',
 'Other',
 'Solaris',
 'Tizen',
 'Ubuntu',
 'Windows',
 'Windows Phone',
 'iOS']

In [13]:
len(db.clicks.find().distinct('device.OS'))

18

---
Unique `Browser`

In [14]:
db.clicks.find().distinct('device.Browser')

['AdsBot-Google',
 'AhrefsBot',
 'Amazon Silk',
 'Android',
 'AppEngine-Google',
 'Apple Mail',
 'BingPreview',
 'BlackBerry WebKit',
 'Chrome',
 'Chrome Mobile',
 'Chrome Mobile WebView',
 'Chrome Mobile iOS',
 'Chromium',
 'Coc Coc',
 'Coveobot',
 'Crosswalk',
 'Dragon',
 'DuckDuckBot',
 'Edge',
 'Edge Mobile',
 'Electron',
 'Epiphany',
 'Facebook',
 'FacebookBot',
 'Firefox',
 'Firefox Mobile',
 'Firefox iOS',
 'HbbTV',
 'HeadlessChrome',
 'HubSpot Crawler',
 'IE',
 'IE Mobile',
 'Iceweasel',
 'Iron',
 'JobBot',
 'Jooblebot',
 'K-Meleon',
 'Kindle',
 'Konqueror',
 'Magus Bot',
 'Mail.ru Chromium Browser',
 'Maxthon',
 'Mobile Safari',
 'Mobile Safari UI/WKWebView',
 'MobileIron',
 'NetFront',
 'Netscape',
 'Opera',
 'Opera Coast',
 'Opera Mini',
 'Opera Mobile',
 'Other',
 'PagePeeker',
 'Pale Moon',
 'PetalBot',
 'PhantomJS',
 'Pinterest',
 'Puffin',
 'Python Requests',
 'QQ Browser',
 'QQ Browser Mobile',
 'Radius Compliance Bot',
 'Safari',
 'Samsung Internet',
 'SeaMonkey',
 'Se

In [15]:
len(db.clicks.find().distinct('device.Browser'))

82

---
Unique `Activity`

In [16]:
db.clicks.find().distinct('Activity')

['click', 'pageload']

----
Number of unique prodcuts

In [17]:
len(db.clicks.find().distinct('ProductID'))

10938

---
# Queries

----

----
### Q1
Get the percentage of documents where there are user ids present. Also get the percentage of documents where the user ids are absent.

***Hint - Keep total documents count in a separate variable beforehand.***

In [18]:
# Find total documents in the collection
total_docs_count = db.clicks.count_documents({})

In [19]:
cur = db.clicks.aggregate([
    # Stage 1 - check if user.UserID is present
    {
        '$match': {'user.UserID': {'$exists': True}}
    },
    # Stage 2 - count the filtered documents
    {
        '$count': 'signed_up'
    },
    # Stage 3 - find the percentage
    {
        '$project': {
            'Percentage_signed_up': {
                '$multiply': [
                    {'$divide': ['$signed_up', total_docs_count]},
                    100
                ]
            },
            'Percentage_not_signed_up': {
                '$multiply': [
                    {'$divide': [
                        {'$subtract': [total_docs_count, '$signed_up']},
                        total_docs_count
                    ]},
                    100
                ]
            }
        }
    }
])

for doc in cur:
    pp.pprint(doc)

{'Percentage_signed_up': 9.873655737704919,
 'Percentage_not_signed_up': 90.12634426229508}


----
### Q2
What was the most popular product?

In [20]:
cur = db.clicks.aggregate([
    # Stage 1 - group on the ProductID field
    {
        '$group': {
            '_id': '$ProductID',
            'Count': {'$sum': 1}
        }
    },
    # Stage 2 - sort the groups based on the Count
    {
        '$sort': {'Count': -1}
    },
    # Stage 3 - limit the result to return the product with the highest count
    {
        '$limit': 1
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': 'Pr100017', 'Count': 157922}


----
### Q3
Count the number of `click` and number of `pageload` for each signed up user. Sort the result in ascending order of the `user.UserID`.

In [21]:
cur = db.clicks.aggregate([
    # Stage 1 - Match documents where user.UserID exists
    {
        '$match': {'user.UserID': {'$exists': True}}
    },
    # Stage 2 - Group by user.UserID and calculate the count of clicks and pageloads
    {
        '$group': {
            '_id': '$user.UserID',
            'ClickCount': {'$sum': {'$cond': [{'$eq': ['$Activity', 'click']}, 1, 0]}},
            'PageLoadCount': {'$sum': {'$cond': [{'$eq': ['$Activity', 'pageload']}, 1, 0]}}
        }
    },
    # Stage 3 - Sort the result in ascending order of user.UserID
    {
        '$sort': {'_id': 1}
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': 'U100002', 'ClickCount': 2, 'PageLoadCount': 3}
{'_id': 'U100003', 'ClickCount': 2, 'PageLoadCount': 2}
{'_id': 'U100004', 'ClickCount': 11, 'PageLoadCount': 17}
{'_id': 'U100005', 'ClickCount': 4, 'PageLoadCount': 6}
{'_id': 'U100006', 'ClickCount': 0, 'PageLoadCount': 1}
{'_id': 'U100007', 'ClickCount': 2, 'PageLoadCount': 4}
{'_id': 'U100008', 'ClickCount': 39, 'PageLoadCount': 30}
{'_id': 'U100009', 'ClickCount': 7, 'PageLoadCount': 13}
{'_id': 'U100012', 'ClickCount': 24, 'PageLoadCount': 15}
{'_id': 'U100013', 'ClickCount': 7, 'PageLoadCount': 10}
{'_id': 'U100014', 'ClickCount': 13, 'PageLoadCount': 4}
{'_id': 'U100015', 'ClickCount': 10, 'PageLoadCount': 4}
{'_id': 'U100016', 'ClickCount': 1, 'PageLoadCount': 6}
{'_id': 'U100017', 'ClickCount': 0, 'PageLoadCount': 1}
{'_id': 'U100018', 'ClickCount': 36, 'PageLoadCount': 13}
{'_id': 'U100019', 'ClickCount': 22, 'PageLoadCount': 7}
{'_id': 'U100020', 'ClickCount': 8, 'PageLoadCount': 4}
{'_id': 'U100023', 'ClickCount': 0,

---
### Q4
Count the number of records per `Country`. Sort the result in descending order of number of records.

In [22]:
cur = db.clicks.aggregate([
    # Stage 1 - Group by user.Country and calculate the count
    {
        '$group': {
            '_id': '$user.Country',
            'RecordCount': {'$sum': 1}
        }
    },
    # Stage 2 - Sort the result in descending order of RecordCount
    {
        '$sort': {'RecordCount': -1}
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': 'India', 'RecordCount': 2663843}
{'_id': 'United States', 'RecordCount': 833389}
{'_id': 'United Kingdom', 'RecordCount': 162125}
{'_id': None, 'RecordCount': 129875}
{'_id': 'Germany', 'RecordCount': 115674}
{'_id': 'Singapore', 'RecordCount': 107007}
{'_id': 'Canada', 'RecordCount': 100649}
{'_id': 'Australia', 'RecordCount': 94601}
{'_id': 'France', 'RecordCount': 86974}
{'_id': 'Turkey', 'RecordCount': 86459}
{'_id': 'Republic of Korea', 'RecordCount': 73706}
{'_id': 'Vietnam', 'RecordCount': 72577}
{'_id': 'Pakistan', 'RecordCount': 68222}
{'_id': 'Brazil', 'RecordCount': 66953}
{'_id': 'Malaysia', 'RecordCount': 62935}
{'_id': 'Netherlands', 'RecordCount': 57270}
{'_id': 'Italy', 'RecordCount': 50987}
{'_id': 'Spain', 'RecordCount': 49761}
{'_id': 'Indonesia', 'RecordCount': 46098}
{'_id': 'Philippines', 'RecordCount': 46006}
{'_id': 'Russia', 'RecordCount': 44945}
{'_id': 'Hong Kong', 'RecordCount': 43101}
{'_id': 'Taiwan', 'RecordCount': 40926}
{'_id': 'Poland', 'Record

----
### Q5
What is the most common/frequently used `OS`? 

And, what is the most common/frequently used `Browser`? 

Also get the count for both.

In [23]:
cur = db.clicks.aggregate([
    # Stage - Sub-pipeline for each result
    {
        '$facet': {
            'Most_used_OS': [
                # Stage 1 - Group by device.OS and calculate the count
                {
                    '$group': {
                        '_id': '$device.OS',
                        'Count': {'$sum': 1}
                    }
                },
                # Stage 2 - Sort the result in descending order of Count
                {
                    '$sort': {'Count': -1}
                },
                # Stage 3 - Limit the result to the first document
                {
                    '$limit': 1
                }
            ],
            'Most_used_Browser': [
                # Stage 1 - Group by device.Browser and calculate the count
                {
                    '$group': {
                        '_id': '$device.Browser',
                        'Count': {'$sum': 1}
                    }
                },
                # Stage 2 - Sort the result in descending order of Count
                {
                    '$sort': {'Count': -1}
                },
                # Stage 3 - Limit the result to the first document
                {
                    '$limit': 1
                }
            ]
        }
    }
])

for doc in cur:
    pp.pprint(doc)

{'Most_used_OS': [{'_id': 'Windows', 'Count': 3931349}],
 'Most_used_Browser': [{'_id': 'Chrome', 'Count': 4360498}]}


---
### Q6
What is most common `OS` and `Browser` combination used by the users? Also get the count for it.

`Example - {'Linux', 'Firefox'}`

In [24]:
cur = db.clicks.aggregate([
    # Stage 1 - Group by device.OS and device.Browser and calculate the count
    {
        '$group': {
            '_id': {
                'OS': '$device.OS',
                'Browser': '$device.Browser'
            },
            'Count': {'$sum': 1}
        }
    },
    # Stage 2 - Sort the result in descending order of Count
    {
        '$sort': {'Count': -1}
    },
    # Stage 3 - Limit the result to the first document
    {
        '$limit': 1
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': {'OS': 'Windows', 'Browser': 'Chrome'}, 'Count': 3589891}


----
### Q7
How many unique users were active in each week from  07/05/2018 - 27/05/2018?

That is, how may unique users visited in the week from 07/05/2018 - 14/05/2018, from 15/05/2018 - 21/05/2018, and so on.

***Hint - You will need the `$addToSet` operator of `$bucket` stage operator and you will need to use the `$size` aggregation operator.***

In [25]:
from datetime import datetime

cur = db.clicks.aggregate([
    # Stage 1 - filter documents for signed up users
    {
        '$match': {
            'user.UserID': {'$exists': True}
        }
    },
    
    # Stage 2 - bucket by each week from 07/05/2018 - 27/05/2018
    {
        '$bucket': {
            'groupBy': '$VisitDateTime',
            'boundaries': [
                datetime(2018, 5, 7),
                datetime(2018, 5, 14),
                datetime(2018, 5, 21),
                datetime(2018, 5, 28)
            ],
            'default': 'Other',
            'output': {
                'Unique_users': {'$addToSet': '$user.UserID'}
            }
        }
    },
    
    # Stage 3 - project the buckets
    {
        '$project': {
            '_id': 1,
            'Unique_users': {'$size': '$Unique_users'}
        }
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': datetime.datetime(2018, 5, 7, 0, 0), 'Unique_users': 18308}
{'_id': datetime.datetime(2018, 5, 14, 0, 0), 'Unique_users': 15522}
{'_id': datetime.datetime(2018, 5, 21, 0, 0), 'Unique_users': 16636}


----
### Q8
From all the unique users who visited between 07/05/2018 - 15/05/2018 dates, who visited the most number of times? Also get a list of unique products viewed by that user in the same duration.

***Hint - Use the `$addToSet` group accumulator operator.***

In [26]:
cur = db.clicks.aggregate([
    # Stage 1 - Filter the documents between the dates and where the user id exists
    {
        '$match': {
            'VisitDateTime': {
                '$gte': datetime(2018, 5, 7),
                '$lte': datetime(2018, 5, 15)
            },
            'user.UserID': {'$exists': True}
        }
    },
    # Stage 2 - Group the documents by user id, count the number of visits, and get an array of unique products viewed
    {
        '$group': {
            '_id': '$user.UserID',
            'Count': {'$sum': 1},
            'Products': {'$addToSet': '$ProductID'}
        }
    },
    # Stage 3 - Sort the group by the count of visits in descending order
    {
        '$sort': {'Count': -1}
    },
    # Stage 4 - Return the user with the highest visit count
    {
        '$limit': 1
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': 'U134751',
 'Count': 1448,
 'Products': ['Pr100166', 'Pr100051', 'Pr100040', 'Pr100123', 'Pr100787']}


---
### Q9
Get the number of times each unique product was viewed by the user from the previous question in the same time duration.

In [27]:
cur = db.clicks.aggregate([
    {
        '$match': {
            'VisitDateTime': {
                '$gte': datetime(2018, 5, 7),
                '$lte': datetime(2018, 5, 15)
            },
            'user.UserID': 'U134751'
        }
    },
    {
        '$group': {
            '_id': '$ProductID',
            'Count': {'$sum': 1}
        }
    }
])

for doc in cur:
    pp.pprint(doc)

{'_id': 'Pr100166', 'Count': 1393}
{'_id': 'Pr100040', 'Count': 6}
{'_id': 'Pr100051', 'Count': 9}
{'_id': 'Pr100787', 'Count': 7}
{'_id': 'Pr100123', 'Count': 33}


------
### Q10
What is the last viewed product by each signed up user till 27/05/2018?

***Hint - Use the `$last` group accumulator operator.***

In [28]:
cur = db.clicks.aggregate([
    # Stage 1 - Filter documents where the user id exists and the visit date is before or on 27/05/2018
    {
        '$match': {
            'user.UserID': {'$exists': True},
            'VisitDateTime': {'$lte': datetime(2018, 5, 27)}
        }
    },
    # Stage 2 - Sort documents by user id and date of visit in descending order
    {
        '$sort': {'user.UserID': 1, 'VisitDateTime': -1}
    },
    # Stage 3 - Group on the user id and find the last product viewed
    {
        '$group': {
            '_id': '$user.UserID',
            'Last_product_viewed': {'$last': '$ProductID'}
        }
    }
],
allowDiskUse=True)

for doc in cur:
    pp.pprint(doc)

{'_id': 'U127783', 'Last_product_viewed': 'Pr100166'}
{'_id': 'U110827', 'Last_product_viewed': 'Pr100859'}
{'_id': 'U113477', 'Last_product_viewed': 'Pr100850'}
{'_id': 'U102010', 'Last_product_viewed': 'Pr100102'}
{'_id': 'U111983', 'Last_product_viewed': 'Pr100102'}
{'_id': 'U133995', 'Last_product_viewed': 'Pr100910'}
{'_id': 'U106501', 'Last_product_viewed': 'Pr100269'}
{'_id': 'U110940', 'Last_product_viewed': 'Pr100095'}
{'_id': 'U128575', 'Last_product_viewed': 'Pr100176'}
{'_id': 'U131955', 'Last_product_viewed': 'Pr100200'}
{'_id': 'U117655', 'Last_product_viewed': 'Pr100128'}
{'_id': 'U106938', 'Last_product_viewed': 'Pr100413'}
{'_id': 'U110356', 'Last_product_viewed': 'Pr102072'}
{'_id': 'U106987', 'Last_product_viewed': 'Pr106054'}
{'_id': 'U127894', 'Last_product_viewed': 'Pr100739'}
{'_id': 'U119102', 'Last_product_viewed': 'Pr101029'}
{'_id': 'U130430', 'Last_product_viewed': 'Pr100910'}
{'_id': 'U104776', 'Last_product_viewed': 'Pr100152'}
{'_id': 'U118889', 'Last_pro